In [1]:
import os
import time
import subprocess

import numpy as np
import scipy.signal
import pandas as pd
import scipy.stats

from tvb.simulator.lab import *
from mne import time_frequency, filter
import plotly.graph_objects as go  # for data visualisation
import plotly.io as pio
from toolbox import timeseriesPlot, FFTplot, FFTpeaks, AEC, PLV, PLI, epochingTool, paramSpace

In [3]:
# This simulation will generate FC for a virtual "Subject".
# Define identifier (i.e. could be 0,1,11,12,...)
subjectid = ".2001LarterBreakspear"
wd=os.getcwd()
main_folder=wd+"\\"+subjectid
ctb_folder=wd+"\\CTB_data\\output\\"
if subjectid not in os.listdir(ctb_folder):
    os.mkdir(ctb_folder+subjectid)
    os.mkdir(main_folder)

emp_subj = "subj04"

# Prepare bimodality test (i.e. Hartigans' dip test in an external R script via python subprocess
# Build subprocess command: [Rscript, script]
# cmd = ['C:\\Program Files\\R\\R-3.6.1\\bin\\Rscript.exe',
#        'C:\\Users\\F_r_e\\PycharmProjects\\brainModels\\diptest\\diptest.R']

simLength = 1000 # ms - relatively long simulation to be able to check for power distribution
samplingFreq = 1000 #Hz
transient=100 # ms to exclude from timeseries due to initial transient

# integrator: dt=T(ms)=1000/samplingFreq(kHz)=1/samplingFreq(HZ)
# integrator = integrators.HeunStochastic(dt=1000/samplingFreq, noise=noise.Additive(nsig=np.array([5e-6])))
integrator = integrators.HeunDeterministic(dt=1000/samplingFreq)

conn = connectivity.Connectivity.from_file(ctb_folder+"CTB_connx66_"+emp_subj+".zip")
conn.weights = conn.scaled_weights(mode="tract")


mon = (monitors.Raw(),)

WARNING  File 'average_orientations' not found in ZIP.
WARNING  File 'cortical' not found in ZIP.
WARNING  File 'hemispheres' not found in ZIP.
WARNING  File 'areas' not found in ZIP.


## Parameters from Roberts (2019)

In [6]:
m = models.LarterBreakspear(C=np.array([0.6]), Iext=np.array([0]),
                            
    QV_max=np.array([1]), QZ_max=np.array([1]),
                            
    TCa=np.array([-0.01]), TK=np.array([0]), TNa=np.array([0.3]),
                            
    VCa=np.array([1]), VK=np.array([-0.7]), VL=np.array([-0.5]), VNa=np.array([0.53]),
                            
    VT=np.array([0]), ZT=np.array([0]),        
                            
    aee=np.array([0.36]),    aei=np.array([2]), aie=np.array([2]), ane=np.array([1]), ani=np.array([0.4]), 
                            
    b=np.array([0.1]),    
                            
    d_Ca=np.array([0.15]), d_K=np.array([0.3]), d_Na=np.array([0.15]), d_V=np.array([0.65]), d_Z=np.array([0.65]), 
                            
    gCa=np.array([1]),     gK=np.array([2]), gL=np.array([0.5]), gNa=np.array([6.7]),     
                            
    phi=np.array([0.7]), rNMDA=np.array([0.25]), t_scale=np.array([0.1]), tau_K=np.array([1]))

# Coupling function
coup = coupling.HyperbolicTangent(a=np.array([1]), b=np.array([1]), midpoint=np.array([0]), sigma=np.array([1]))
conn.speed=np.array([1])

# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][:, 0, :, 0].T
raw_time = output[0][0][:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")

# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, mode="inline")
# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, mode="inline")

Simulation time: 0.84 sec


## From Endo 2020

In [8]:
m = models.LarterBreakspear(C=np.array([0.35]), Iext=np.array([0]),
                            
    QV_max=np.array([1]), QZ_max=np.array([1]),
                            
    TCa=np.array([-0.01]), TK=np.array([0]), TNa=np.array([0.3]),
                            
    VCa=np.array([1]), VK=np.array([-0.7]), VL=np.array([-0.5]), VNa=np.array([0.53]),
                            
    VT=np.array([0]), ZT=np.array([0]),        
                            
    aee=np.array([0.36]),    aei=np.array([2]), aie=np.array([2]), ane=np.array([1]), ani=np.array([0.4]), 
                            
    b=np.array([0.1]),    
                            
    d_Ca=np.array([0.15]), d_K=np.array([0.3]), d_Na=np.array([0.15]), d_V=np.array([0.68]), d_Z=np.array([0.68]), 
                            
    gCa=np.array([1]),     gK=np.array([2]), gL=np.array([0.5]), gNa=np.array([6.7]),     
                            
    phi=np.array([0.7]), rNMDA=np.array([0.25]), t_scale=np.array([0.1]), tau_K=np.array([1]))

# Coupling function
coup = coupling.HyperbolicTangent(a=np.array([1]), b=np.array([1]), midpoint=np.array([0]), sigma=np.array([1]))
conn.speed=np.array([1])

# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][:, 0, :, 0].T
raw_time = output[0][0][:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")

# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, mode="inline")
# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, mode="inline")

Simulation time: 0.87 sec


## from Larter-Breakspear 2003b

In [9]:
m = models.LarterBreakspear(C=np.array([0.35]), Iext=np.array([0]),
                            
    QV_max=np.array([1]), QZ_max=np.array([1]),
                            
    TCa=np.array([-0.01]), TK=np.array([0]), TNa=np.array([0.3]),
                            
    VCa=np.array([1]), VK=np.array([-0.7]), VL=np.array([-0.5]), VNa=np.array([0.53]),
                            
    VT=np.array([0]), ZT=np.array([0]),        
                            
    aee=np.array([0.36]),    aei=np.array([2]), aie=np.array([2]), ane=np.array([1]), ani=np.array([0.4]), 
                            
    b=np.array([0.1]),    
                            
    d_Ca=np.array([0.15]), d_K=np.array([0.3]), d_Na=np.array([0.15]), d_V=np.array([0.605]), d_Z=np.array([0.7]), 
                            
    gCa=np.array([1.1]),     gK=np.array([2]), gL=np.array([0.5]), gNa=np.array([6.7]),     
                            
    phi=np.array([0.7]), rNMDA=np.array([0.25]), t_scale=np.array([0.1]), tau_K=np.array([1]))

# Coupling function
coup = coupling.HyperbolicTangent(a=np.array([1]), b=np.array([1]), midpoint=np.array([0]), sigma=np.array([1]))
conn.speed=np.array([1])

# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][:, 0, :, 0].T
raw_time = output[0][0][:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")

# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, mode="inline")
# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, mode="inline")

Simulation time: 0.88 sec


## TVB default parameters

In [10]:
m = models.LarterBreakspear(C=np.array([0.1]), Iext=np.array([0]),
    QV_max=np.array([1]), QZ_max=np.array([1]),
    TCa=np.array([-0.01]), TK=np.array([0]), TNa=np.array([0.3]),
    VCa=np.array([1]), VK=np.array([-0.7]), VL=np.array([-0.5]), VNa=np.array([0.53]),
    VT=np.array([0]), ZT=np.array([0]),                          
    aee=np.array([0.4]),    aei=np.array([2]), aie=np.array([2]), ane=np.array([1]), ani=np.array([0.4]), b=np.array([0.1]),                      
    d_Ca=np.array([0.15]), d_K=np.array([0.3]), d_Na=np.array([0.15]), d_V=np.array([0.65]),     d_Z=np.array([0.7]),                      
    gCa=np.array([1.1]),     gK=np.array([2]), gL=np.array([0.5]), gNa=np.array([6.7]),                       
    phi=np.array([0.7]), rNMDA=np.array([0.25]),       t_scale=np.array([0.1]), tau_K=np.array([1]))

# Coupling function
coup = coupling.HyperbolicTangent(a=np.array([1]), b=np.array([1]), midpoint=np.array([0]), sigma=np.array([1]))

# Run simulation
tic0=time.time()
sim = simulator.Simulator(model=m, connectivity=conn, coupling=coup,  integrator=integrator, monitors=mon)
sim.configure()

output = sim.run(simulation_length=simLength)
print("Simulation time: %0.2f sec" % (time.time() - tic0,))
# Extract data cutting initial transient
raw_data = output[0][1][:, 0, :, 0].T
raw_time = output[0][0][:]
regionLabels = conn.region_labels
regionLabels=list(regionLabels)
regionLabels.insert(0,"AVG")

# average signals to obtain mean signal frequency peak
data = np.asarray([np.average(raw_data, axis=0)])
data = np.concatenate((data, raw_data), axis=0)  # concatenate mean signal: data[0]; with raw_data: data[1:end]

# Check initial transient and cut data
timeseriesPlot(data[0:10], raw_time, regionLabels, main_folder, mode="inline")
# Fourier Analysis plot
FFTplot(data[0:10], simLength, regionLabels, main_folder, mode="inline")

Simulation time: 0.81 sec
